# Free Kaggle Notebook V3 - 21 January 2024
## Please read instructions carefully
### Most updated version with config of this notebook will be on > 
### https://www.patreon.com/posts/ip-adapter-0-app-95759342
### Tutorial Video  > vide coming very soon hopefully

In [ ]:
!pip install opencv-python-headless
!pip install gradio
!pip install diffusers
!pip install insightface
!pip install onnxruntime-gpu
!pip install git+https://github.com/tencent-ailab/IP-Adapter.git
!pip install transformers
!pip install einops
!pip install accelerate
!pip install xformers
!pip install omegaconf
!pip install flask
!pip install pyngrok
!wget https://huggingface.co/MonsterMMORPG/Stable-Diffusion/resolve/main/web-ui.py

In [ ]:
import os
import requests
from tqdm import tqdm

def create_directory(path):
    """Create directory if it does not exist."""
    if not os.path.exists(path):
        os.makedirs(path)
        print(f"Directory created: {path}")
    else:
        print(f"Directory already exists: {path}")

def download_file(url, folder_path):
    print(f"{url}")
    """Download a file from a given URL to a specified folder."""
    local_filename = url.split('/')[-1]
    local_filepath = os.path.join(folder_path, local_filename)

    # Stream download to handle large files
    with requests.get(url, stream=True) as r:
        r.raise_for_status()
        total_size_in_bytes = int(r.headers.get('content-length', 0))
        block_size = 1024 # 1 Kibibyte
        progress_bar = tqdm(total=total_size_in_bytes, unit='iB', unit_scale=True)
        with open(local_filepath, 'wb') as f:
            for data in r.iter_content(block_size):
                progress_bar.update(len(data))
                f.write(data)
        progress_bar.close()

    if total_size_in_bytes != 0 and progress_bar.n != total_size_in_bytes:
        print("ERROR, something went wrong")
    else:
        print(f"Downloaded {local_filename} to {folder_path}")

# Define the folders and their corresponding file URLs
folders_and_files = {
    os.path.join("adapters"): [
        "https://huggingface.co/h94/IP-Adapter-FaceID/resolve/main/ip-adapter-faceid-plusv2_sdxl.bin",
        "https://huggingface.co/h94/IP-Adapter-FaceID/resolve/main/ip-adapter-faceid-plusv2_sd15.bin"
    ],
	os.path.join("h94","IP-Adapter","models","image_encoder"): [
        "https://huggingface.co/h94/IP-Adapter/resolve/main/models/image_encoder/config.json",
		"https://huggingface.co/h94/IP-Adapter/resolve/main/models/image_encoder/model.safetensors"
    ]
}

# Perform the download process
for folder, files in folders_and_files.items():
    create_directory(folder)
    for file_url in files:
        download_file(file_url, folder)

In [ ]:
# run this to be able to start using temp folder
!mkdir /kaggle/temp

In [ ]:
# how to download civitAI models example. watch tutorial to understand
!wget "https://civitai.com/api/download/models/125771" -O /kaggle/temp/toon.safetensors

### First you need to register and get a token. 
### I used gmail register >
### https://dashboard.ngrok.com/get-started/your-authtoken
### Skipped authenticator not necessary
### [Click here](https://cdn-uploads.huggingface.co/production/uploads/6345bd89fe134dfd7a0dba40/eRmm7HjCcKhqsTNTJXy9E.png) to see how a token looks like you need to get

In [ ]:
## first put your ngrok token to the below and then run this code
## it will give a link like this at below : https://2fc5-34-134-226-xxx.ngrok-free.app
## open it and then run web ui 
## after web ui started click visit site
import os
import threading

from flask import Flask
from pyngrok import ngrok, conf

conf.get_default().auth_token = "PUT_YOUR_NGROK_TOKEN_HERE"

os.environ["FLASK_ENV"] = "development"

app = Flask(__name__)

public_url = ngrok.connect(7860).public_url
print(" * ngrok tunnel \"{}\" -> \"http://127.0.0.1:{}/\"".format(public_url, 7860))

app.config["BASE_URL"] = public_url

@app.route("/")
def index():
    return "Hello from Colab!"

threading.Thread(target=app.run, kwargs={"use_reloader": False}).start()


In [ ]:
# if you ever restart this cell, first run 1 time above ngrok cell open it
# after web ui started click visit site on ngrok
!python web-ui.py

In [ ]:
!rm -r /kaggle/working/generated_images.zip
%cd /kaggle/working/outputs
!zip -r /kaggle/working/generated_images.zip *
%cd -